# <a id='toc1_'></a>[PCE:Couplage de Rdkit Crest-xTB avec AlGORITHME DE SCHARBER ](#toc0_)

1. **MVOTO KONGO Patrick Sorrel**, sorrel.mvoto@facsciences-uy1.cm
    * Department of Physics, Faculty of Science, University of Yaounde I 
Etudiant de Master au Laboratoire de 
    * Physique Atomique Moleculaire et Biophysique

JUIN 2024

* Nos travaux de mémoire sont basés sur le flux de travail de Tartarus. L'algorithme est le suivant :
<img src="./Graphics/tartarusoverview.png" width="1500"></center>

 Une illustration du cadre Tartarus, mettant en évidence les tâches de conception réelles qui sont définies et associées à des flux de travail et des ensembles de données de simulation dans Tartarus




*  Notre objectif de recherche consiste à concevoir des petites molécules dotées de propriétés électroniques spécifiques, notamment des molécules capables d'effectuer la séparation des charges, inspirées de la conception photovoltaïque organique (OPV). Nous avons deux tâches individuelles :

- Recherche d'une molécule donneuse organique à utiliser avec l'ester méthylique de l'acide l'ester méthylique de
    l'acide ${[6,6]­phényl­C61­butyrique(PCBM)}$.
- Recherche d'une molécule accepteuse à utiliser dans des dispositifs basés sur le poly[N­90­heptadécanyl­2,7­carbazole­alt­5,5­(40,70­di­2­thiényl­20,10,30­benzothiaMachine  (PCDTBT)).

*  Notre travail actuel porte sur le modèle ci-dessous :
<img src="./opv.png" width="2000"></center>

 schématique du flux de travail de simulation de propriétés pour la conception de références photovoltaïques organiques

###  <a id='toc1_4_'></a>[Tension de circuit ouvert(V_oc)](#toc0_)


 <div  class="alert alert-info">
Représentent la tension maximale qu’une cellule solaire peut appliquer a une charge externes

* Ecart entre la HOMO du composé donneur et la LUMO du composé accepteur

* Influencée par la recombinaison des charges qui ne peut être totalement évitée 

</div> 
        

\begin{equation}
\begin{split}




{V_{oc}}={\frac{1}{e}|E^{Do}HOMO|-|E^{AC}LUMO| -0.3}\\.

\end{split}
\end{equation}

* ${e}$ represente la charge de l'electrons 
* $E^{Do}HOMO$ represente l'énergie  Homo du donneur sa valeur maximale dans les travaux CEP est estimée ${-3,62 eV}$  et donc la gamme de valeurs normales se situe entre ${[-5.7 ; -4.5]eV}$
* $E^{AC}LUMO$ represente l'énergie Lumo de l'accepteur sa valeur maximale dans les travaux CEP est estimée ${-1,15 eV}$ et donc la gamme de valeurs normales se situe entre ${[-4 ; -3]eV}$
* -0.3 est la tension seuil en dessous du quelle il n'y'a separation des exciton

In [2]:
import os
import pandas as pd
import rdkit
from rdkit import Chem
from rdkit.Chem import rdDetermineBonds
from rdmc.mol import RDKitMol
from rdmc.view import mol_viewer
from rdkit import Chem
from rdkit.Chem.Draw import IPythonConsole
from pyscf.data import nist

au2ev = nist.HARTREE2EV


# Paramètres
input_dir = 'GDB-9'  # Dossier contenant les fichiers .xyz d'origine
output_dir = 'GDB-V2024'  # Dossier où seront créés les nouveaux fichiers .xyz
output_file = 'Patrick_GDB-9_dataframe.csv'  # Nom du fichier CSV pour le dataframe
max_files = 1074  # Nombre maximum de fichiers à traiter

# Créer le dossier de sortie s'il n'existe pas
if not os.path.exists(output_dir):
    os.makedirs(output_dir)

# Fonction pour nettoyer les fichiers XYZ
def cleanup_GDB9_xyz(fname):
    ind = open(fname).readlines()
    nAts = int(ind[0])
    smi = ind[-2].split()[-1]
    ind[1] = '\n'
    ind = ind[:nAts+2]
    for i in range(2, nAts+2):
        l = ind[i]
        l = l.split()
        l.pop(-1)
        ind[i] = '\t'.join(l) + '\n'
    ind = ''.join(ind)
    return ind, smi

# Initialiser la liste pour le dataframe
data = []

# Parcourir les 1000 premiers fichiers .xyz d'origine
for i in range(1, max_files + 1):
    filename = f'dsgdb9nsd_{i:06d}.xyz'
    filepath = os.path.join(input_dir, filename)

    if os.path.exists(filepath):
        # Construire le nouveau nom de fichier
        new_filename = f'GDB{i}.xyz'
        new_filepath = os.path.join(output_dir, new_filename)

        # Extraire les coordonnées XYZ, le nom du monde GDB, et les propriétés
        with open(filepath, 'r') as f:
            lines = f.readlines()
            num_atoms = int(lines[0].strip())
            world_name = lines[1].strip().split('\t')[0]
            properties = [float(x) for x in lines[1].strip().split('\t')[1:]]
            xyz_coords = [line.strip().split() for line in lines[2:2+num_atoms]]

        # Utiliser la fonction pour nettoyer et obtenir les coordonnées XYZ
        ind, smi = cleanup_GDB9_xyz(filepath)

        # Écrire les nouvelles coordonnées XYZ dans le nouveau fichier
        with open(new_filepath, 'w') as f:
            f.write(f'{num_atoms}\n')
            f.write('\n')
            for row in xyz_coords:
                formatted_row = '{:<2} {:>15} {:>15} {:>15}\n'.format(row[0], row[1], row[2], row[3])
                f.write(formatted_row)

        try:
            # Générer les objets RDKit
            raw_mol = Chem.MolFromXYZBlock(ind)
            if raw_mol is None:
                raise ValueError("MolFromXYZBlock failed to create a molecule")

            bond_mol = Chem.Mol(raw_mol)
            rdDetermineBonds.DetermineBonds(bond_mol, charge=0)
            smiles = Chem.MolToSmiles(Chem.RemoveHs(bond_mol))
            smiles_c = Chem.CanonSmiles(smi)
            homo= properties[5]
            lumo= properties[6]
            gap= properties[7]
            # Ajouter les informations au dataframe
            data.append({
                'smiles_key': world_name,
                'smiles': smiles,
                'smiles_c': smiles_c,
                'mol': bond_mol,
                'HOMO(HARTREE)': homo,
                'LUMO(HARTREE)': lumo,
                'gap(HARTREE)': gap,
                'HOMO(eV)':homo*au2ev ,
                'LUMO(eV)': lumo*au2ev ,
                'gap(ev)': gap*au2ev ,
            })
        except Exception as e:
            print(f"Error processing file {filename}: {e}")
            continue

# Créer le dataframe et l'enregistrer dans un fichier CSV
properties_df = pd.DataFrame(data)
# Remarque : RDKit Mol objects ne peuvent pas être directement enregistrés dans un fichier CSV. 
# Vous pouvez soit les convertir en un format sérialisé, soit les omettr
properties_df.drop(columns=['mol']).to_csv(output_file, index=False)

Error processing file dsgdb9nsd_000105.xyz: Valence of atom 1 is 5, which is larger than the allowed maximum, 4
Error processing file dsgdb9nsd_000106.xyz: Valence of atom 1 is 5, which is larger than the allowed maximum, 4
Error processing file dsgdb9nsd_000212.xyz: MolFromXYZBlock failed to create a molecule
Error processing file dsgdb9nsd_000271.xyz: Python argument types in
    rdkit.Chem.rdmolfiles.MolToSmiles(NoneType, int)
did not match C++ signature:
    MolToSmiles(RDKit::ROMol mol, bool isomericSmiles=True, bool kekuleSmiles=False, int rootedAtAtom=-1, bool canonical=True, bool allBondsExplicit=False, bool allHsExplicit=False, bool doRandom=False)
    MolToSmiles(RDKit::ROMol mol, RDKit::SmilesWriteParams params)
Error processing file dsgdb9nsd_000282.xyz: Python argument types in
    rdkit.Chem.rdmolfiles.MolToSmiles(NoneType, int)
did not match C++ signature:
    MolToSmiles(RDKit::ROMol mol, bool isomericSmiles=True, bool kekuleSmiles=False, int rootedAtAtom=-1, bool canon

In [3]:
df=properties_df.iloc[0:110,:]
df

smiles_key        smiles smiles_c  \
0        gdb 1             C        C   
1        gdb 2             N        N   
2        gdb 3             O        O   
3        gdb 4           C#C      C#C   
4        gdb 5           C#N      C#N   
..         ...           ...      ...   
105    gdb 108       C#CCC#N  C#CCC#N   
106    gdb 109       N#CCC#N  N#CCC#N   
107    gdb 110       C#CCC=O  C#CCC=O   
108    gdb 111       N#CCC=O  N#CCC=O   
109    gdb 112  [H]/N=C/NC=O  N=CNC=O   

                                                  mol  HOMO(HARTREE)  \
0    <rdkit.Chem.rdchem.Mol object at 0x7363a25f4540>        -0.3877   
1    <rdkit.Chem.rdchem.Mol object at 0x7363a25f44f0>        -0.2570   
2    <rdkit.Chem.rdchem.Mol object at 0x7363a26485e0>        -0.2928   
3    <rdkit.Chem.rdchem.Mol object at 0x7363a16868b0>        -0.2845   
4    <rdkit.Chem.rdchem.Mol object at 0x7363a1623450>        -0.3604   
..                                                ...            ...   
105  <rdkit.Chem.rdchem.Mol object at 0x7363a15b34a0>        -0.2911   
106  <rdkit.Chem.rdchem.Mol object at 0x7363a15b3770>        -0.3494   
107  <rdkit.Chem.rdchem.Mol object at 0x7363a15b3720>        -0.2583   
108  <rdkit.Chem.rdchem.Mol object at 0x7363a15b3680>        -0.2868   
109  <rdkit.Chem.rdchem.Mol object at 0x7363a15b32c0>        -0.2491   

     LUMO(HARTREE)  gap(HARTREE)   HOMO(eV)  LUMO(eV)    gap(ev)  
0           0.1171        0.5048 -10.549854  3.186453  13.736308  
1           0.0829        0.3399  -6.993326  2.255824   9.249150  
2           0.0687        0.3615  -7.967494  1.869422   9.836916  
3           0.0506        0.3351  -7.741639  1.376896   9.118535  
4           0.0191        0.3796  -9.806984  0.519737  10.329442  
..             ...           ...        ...       ...        ...  
105         0.0111        0.3022  -7.921234  0.302046   8.223281  
106        -0.0151        0.3344  -9.507658 -0.410892   9.099487  
107        -0.0337        0.2245  -7.028701 -0.917024   6.108956  
108        -0.0568        0.2300  -7.804226 -1.545607   6.258619  
109        -0.0216        0.2276  -6.778356 -0.587766   6.193311  

[110 rows x 10 columns]

In [4]:
import xtb

In [5]:
!crest --version


       |                                            |
       |                 C R E S T                  |
       |                                            |
       |  Conformer-Rotamer Ensemble Sampling Tool  |
       |          based on the GFN methods          |
       |             P.Pracht, S.Grimme             |
       |          Universitaet Bonn, MCTC           |
       Version 2.12,   Thu 19. Mai 16:32:32 CEST 2022
  Using the xTB program. Compatible with xTB version 6.4.0

   Cite work conducted with this code as

   • P.Pracht, F.Bohle, S.Grimme, PCCP, 2020, 22, 7169-7192.
   • S.Grimme, JCTC, 2019, 15, 2847-2862.

   and for works involving QCG as

   • S.Spicher, C.Plett, P.Pracht, A.Hansen, S.Grimme,
     JCTC, 2022, 18 (5), 3174-3189.

   with help from:
   C.Bannwarth, F.Bohle, S.Ehlert, S.Grimme,
   C.Plett, P.Pracht, S.Spicher

   This program is distributed in the hope that it will be useful,
   but WITHOUT ANY WARRANTY; without even the implied warranty of
   M

In [6]:
import os, sys
import inspect
from pathlib import Path
import tempfile
from utils import run_command

import rdkit
from rdkit.Chem import AllChem, DataStructs
from rdkit.Chem import AllChem as Chem
from rdkit.Chem import RDConfig
sys.path.append(os.path.join(RDConfig.RDContribDir, 'SA_Score'))
import sascorer

import numpy as np
import torch
import torch.nn as nn

In [7]:
MY_GDB9_DATA = os.path.join(os.getcwd(), 'MY_GDB9_DATA')
os.makedirs(MY_GDB9_DATA, exist_ok=True)


In [8]:
import os
import pandas as pd
from rdkit import Chem


def calculate_properties(df, working_dir):
    """
    Calculates molecular properties for SMILES strings in a DataFrame,
    handling xtb convergence errors and filtering unsuccessful molecules.

    Args:
        df (pandas.DataFrame): A DataFrame containing a "smiles" column.
        working_dir (str): The directory to use for calculations and temporary files.

    Returns:
        pandas.DataFrame: A DataFrame containing calculated properties for successful molecules.
    """

    dtb = []
    yesso = ["GAP_xtb(eV)","MO_DIP_xtb (eV)","HOMO_xtb(eV)","LUMO_xtb(eV)"]

    filtered_df = df.copy()  # Create a copy to avoid modifying the original DataFrame

    for i in range(len(filtered_df)):
        smiles = filtered_df.loc[i, "smiles"]
        smiles_key = filtered_df.loc[i, "smiles_key"]
         
        mol = Chem.MolFromSmiles(smiles)
        mol = Chem.AddHs(mol)
        charge = Chem.rdmolops.GetFormalCharge(mol)
        atom_number = mol.GetNumAtoms()

        # Create a single directory for all calculations
        directory = os.path.join(working_dir, smiles_key )
        os.makedirs(directory, exist_ok=True)

        # Change directory for calculations
        os.chdir(directory)
        system = lambda x: run_command(x, verbose=5)

        # Write the smile to a file
        with open('test.smi', 'w') as f:
            f.write(smiles)

        # Prepare the input file
        os.system('obabel test.smi --gen3D -O test.xyz')

        # Run the preliminary xtb: 
        command_pre = 'CHARGE={};xtb {} --gfn 2 --opt normal -c $CHARGE --iterations 4000'.format(charge, 'test.xyz')
       
        try:
            # Run xtb with error handling
            result = os.system(command_pre)
            if result != 0:
                print(f"xtb preliminary optimization failed for '{smiles}'. Skipping.")
                filtered_df.drop(i, inplace=True)  # Remove molecule from DataFrame
                continue  # Skip to the next molecule
        except Exception as e:
            print(f"An error occurred while running xtb for '{smiles}': {e}")
            filtered_df.drop(i, inplace=True)  # Remove molecule from DataFrame
            continue  # Skip to the next molecule
            

        os.system("rm ./gfnff_charges ./gfnff_topo")  # Optional removal
         
        # Run crest conformer ensemble
        command_crest = 'CHARGE={};crest {} -gff -mquick -chrg $CHARGE --noreftopo'.format(charge, 'xtbopt.xyz')
        os.system(command_crest)
       
        os.system('rm ./gfnff_charges ./gfnff_topo')  # Optional removal
        os.system('head -n {} crest_conformers.xyz > crest_best.xyz'.format(atom_number+2))

        # Run the calculation
        command = 'CHARGE={};xtb {} --opt normal -c $CHARGE --iterations 4000 > out_dump'.format(charge, 'crest_best.xyz')

        try:
            # Run xtb with error handling
            result = os.system(command)
            if result != 0:
                print(f"xtb final optimization failed for '{smiles}'. Skipping.")
                filtered_df.drop(i, inplace=True)  # Remove molecule from DataFrame
                continue  # Skip to the next molecule
        except Exception as e:
            print(f"An error occurred while running xtb for '{smiles}': {e}")
            filtered_df.drop(i, inplace=True)  # Remove molecule from DataFrame
            continue  # Skip to the next molecule

        # Read the output (implementation details omitted)
        # Read the output
        with open('./out_dump', 'r') as f:
            text_content = f.readlines()
        output_index = [i for i in range(len(text_content)) if 'Property Printout' in text_content[i]]
        text_content = text_content[output_index[0]:]
        homo_data = [x for x in text_content if '(HOMO)' in x]
        lumo_data = [x for x in text_content if '(LUMO)' in x]
        homo_lumo_gap = [x for x in text_content if 'HOMO-LUMO GAP' in x]
        mol_dipole = [text_content[i:i+4] for i, x in enumerate(text_content) if 'molecular dipole:' in x]
        lumo_val = float(lumo_data[0].split(' ')[-2])
        homo_val = float(homo_data[0].split(' ')[-2])
        homo_lumo_val = float(homo_lumo_gap[0].split(' ')[-5])
        mol_dipole_val = float(mol_dipole[0][-1].split(' ')[-1])



        # Write the properties to a single file (modify as needed)
        with open(os.path.join(directory, 'properties.txt'), 'a') as f:
            f.write(f'SMILES: {smiles}\n')
            f.write(f'LUMO: {lumo_val}\n')
            f.write(f'HOMO: {homo_val}\n')
            f.write(f'HOMO-LUMO GAP: {homo_lumo_val}\n')
        dtb.append([homo_lumo_val, mol_dipole_val, homo_val, lumo_val])
        os.chdir('..')

    df_xtb = pd.DataFrame(dtb, columns=yesso)
    return df_xtb

df_xtb = calculate_properties(df, MY_GDB9_DATA)

1 molecule converted


      -----------------------------------------------------------      
     |                   =====================                   |     
     |                           x T B                           |     
     |                   =====================                   |     
     |                         S. Grimme                         |     
     |          Mulliken Center for Theoretical Chemistry        |     
     |                    University of Bonn                     |     
      -----------------------------------------------------------      

   * xtb version 6.5.1 (fef0646) compiled by 'conda@b96dff2e9fd6' on 2023-01-04

   xtb is free software: you can redistribute it and/or modify it under
   the terms of the GNU Lesser General Public License as published by
   the Free Software Foundation, either version 3 of the License, or
   (at your option) any later version.
   
   xtb is distributed in the hope that it will be useful,
   but WITHOUT ANY WARRANTY; w

normal termination of xtb
Note: The following floating-point exceptions are signalling: IEEE_DENORMAL
rm: cannot remove './gfnff_charges': No such file or directory
rm: cannot remove './gfnff_topo': No such file or directory


 done.
 Calculating NCI flexibility... done.
     covalent flexibility measure :   0.000
 non-covalent flexibility measure :   0.960
 flexibility measure :   0.000
 t(MTD) / ps    :     2.5
 Σ(t(MTD)) / ps :    15.0 (6 MTDs)

-------------------------------------
Starting a trial MTD to test settings
-------------------------------------
 Estimated runtime for one MTD (2.5 ps) on a single thread: 2 sec
 Estimated runtime for a batch of 6 MTDs on 4 threads: 5 sec

 list of Vbias parameters applied:
$metadyn    0.00200   1.000
$metadyn    0.00100   1.000
$metadyn    0.00200   0.500
$metadyn    0.00100   0.500
$metadyn    0.00200   0.250
$metadyn    0.00100   0.250

*******************************************************************************************
**                        N E W    I T E R A T I O N    C Y C L E                        **
*******************************************************************************************

            MTD Simulations 

     |         Meta-M

normal termination of xtb
Note: The following floating-point exceptions are signalling: IEEE_DENORMAL
1 molecule converted


...

normal termination of xtb
Note: The following floating-point exceptions are signalling: IEEE_DENORMAL
1 molecule converted


      -----------------------------------------------------------      
     |                   =====================                   |     
     |                           x T B                           |     
     |                   =====================                   |     
     |                         S. Grimme                         |     
     |          Mulliken Center for Theoretical Chemistry        |     
     |                    University of Bonn                     |     
      -----------------------------------------------------------      

   * xtb version 6.5.1 (fef0646) compiled by 'conda@b96dff2e9fd6' on 2023-01-04

   xtb is free software: you can redistribute it and/or modify it under
   the terms of the GNU Lesser General Public License as published by
   the Free Software Foundation, either version 3 of the License, or
   (at your option) any later version.
   
   xtb is distributed in the hope that it will be useful,
   but WITHOUT ANY WARRANTY; w

normal termination of xtb
Note: The following floating-point exceptions are signalling: IEEE_DENORMAL
rm: cannot remove './gfnff_charges': No such file or directory
rm: cannot remove './gfnff_topo': No such file or directory


 done.
 Calculating NCI flexibility... done.
     covalent flexibility measure :   0.225
 non-covalent flexibility measure :   0.880
 flexibility measure :   0.321
 t(MTD) / ps    :     2.5
 Σ(t(MTD)) / ps :    15.0 (6 MTDs)

-------------------------------------
Starting a trial MTD to test settings
-------------------------------------
 Estimated runtime for one MTD (2.5 ps) on a single thread: 7 sec
 Estimated runtime for a batch of 6 MTDs on 4 threads: 13 sec

 list of Vbias parameters applied:
$metadyn    0.00200   1.000
$metadyn    0.00100   1.000
$metadyn    0.00200   0.500
$metadyn    0.00100   0.500
$metadyn    0.00200   0.250
$metadyn    0.00100   0.250

*******************************************************************************************
**                        N E W    I T E R A T I O N    C Y C L E                        **
*******************************************************************************************

            MTD Simulations 

     |         Meta-

normal termination of xtb
Note: The following floating-point exceptions are signalling: IEEE_DENORMAL


In [9]:
df2=df_xtb
df2

GAP_xtb(eV)  MO_DIP_xtb (eV)  HOMO_xtb(eV)  LUMO_xtb(eV)
0      17.372269            0.000      -12.7208        4.6515
1      12.228695            1.786      -10.5062        1.7225
2      14.400088            2.218      -12.1474        2.2527
3       7.287097            0.003      -11.5117       -4.2246
4       5.950167            2.622      -12.2418       -6.2916
..           ...              ...           ...           ...
105     5.595991            3.596      -11.4653       -5.8694
106     5.471844            4.000      -12.2363       -6.7644
107     3.733713            2.507      -11.1124       -7.3787
108     3.853747            1.578      -11.8488       -7.9951
109     3.520791            4.359      -10.9121       -7.3913

[110 rows x 4 columns]

In [22]:
df_dFT=pd.concat([df,df_xtb ], axis=1)
df_dFT

smiles_key        smiles smiles_c  \
0        gdb 1             C        C   
1        gdb 2             N        N   
2        gdb 3             O        O   
3        gdb 4           C#C      C#C   
4        gdb 5           C#N      C#N   
..         ...           ...      ...   
105    gdb 108       C#CCC#N  C#CCC#N   
106    gdb 109       N#CCC#N  N#CCC#N   
107    gdb 110       C#CCC=O  C#CCC=O   
108    gdb 111       N#CCC=O  N#CCC=O   
109    gdb 112  [H]/N=C/NC=O  N=CNC=O   

                                                  mol  HOMO(HARTREE)  \
0    <rdkit.Chem.rdchem.Mol object at 0x7363a25f4540>        -0.3877   
1    <rdkit.Chem.rdchem.Mol object at 0x7363a25f44f0>        -0.2570   
2    <rdkit.Chem.rdchem.Mol object at 0x7363a26485e0>        -0.2928   
3    <rdkit.Chem.rdchem.Mol object at 0x7363a16868b0>        -0.2845   
4    <rdkit.Chem.rdchem.Mol object at 0x7363a1623450>        -0.3604   
..                                                ...            ...   
105  <rdkit.Chem.rdchem.Mol object at 0x7363a15b34a0>        -0.2911   
106  <rdkit.Chem.rdchem.Mol object at 0x7363a15b3770>        -0.3494   
107  <rdkit.Chem.rdchem.Mol object at 0x7363a15b3720>        -0.2583   
108  <rdkit.Chem.rdchem.Mol object at 0x7363a15b3680>        -0.2868   
109  <rdkit.Chem.rdchem.Mol object at 0x7363a15b32c0>        -0.2491   

     LUMO(HARTREE)  gap(HARTREE)   HOMO(eV)  LUMO(eV)    gap(ev)  GAP_xtb(eV)  \
0           0.1171        0.5048 -10.549854  3.186453  13.736308    17.372269   
1           0.0829        0.3399  -6.993326  2.255824   9.249150    12.228695   
2           0.0687        0.3615  -7.967494  1.869422   9.836916    14.400088   
3           0.0506        0.3351  -7.741639  1.376896   9.118535     7.287097   
4           0.0191        0.3796  -9.806984  0.519737  10.329442     5.950167   
..             ...           ...        ...       ...        ...          ...   
105         0.0111        0.3022  -7.921234  0.302046   8.223281     5.595991   
106        -0.0151        0.3344  -9.507658 -0.410892   9.099487     5.471844   
107        -0.0337        0.2245  -7.028701 -0.917024   6.108956     3.733713   
108        -0.0568        0.2300  -7.804226 -1.545607   6.258619     3.853747   
109        -0.0216        0.2276  -6.778356 -0.587766   6.193311     3.520791   

     MO_DIP_xtb (eV)  HOMO_xtb(eV)  LUMO_xtb(eV)  
0              0.000      -12.7208        4.6515  
1              1.786      -10.5062        1.7225  
2              2.218      -12.1474        2.2527  
3              0.003      -11.5117       -4.2246  
4              2.622      -12.2418       -6.2916  
..               ...           ...           ...  
105            3.596      -11.4653       -5.8694  
106            4.000      -12.2363       -6.7644  
107            2.507      -11.1124       -7.3787  
108            1.578      -11.8488       -7.9951  
109            4.359      -10.9121       -7.3913  

[110 rows x 14 columns]

In [23]:
df4 = pd.DataFrame()
for i in range(len(df)):
    dif_homo= abs(df2.at[i,"HOMO_xtb(eV)"] - df.at[i, 'HOMO(eV)'])
    dif_lumo =abs(df2.at[i,"LUMO_xtb(eV)"] - df.at[i, 'LUMO(eV)'])
    dif_gap = abs(df2.at[i,"GAP_xtb(eV)"] - df.at[i, 'gap(ev)'])
    df4.at[i,'dif_homo(kcal/mol)'] = dif_homo * 627.5
    df4.at[i,'dif_lumo(kcal/mol)'] =  dif_lumo * 627.5
    df4.at[i,'dif_gap(kcal/mol)'] = dif_gap  * 627.5

In [24]:
DF_dFT=pd.concat([df_dFT, df4], axis=1)

In [25]:
DF_dFT

smiles_key        smiles smiles_c  \
0        gdb 1             C        C   
1        gdb 2             N        N   
2        gdb 3             O        O   
3        gdb 4           C#C      C#C   
4        gdb 5           C#N      C#N   
..         ...           ...      ...   
105    gdb 108       C#CCC#N  C#CCC#N   
106    gdb 109       N#CCC#N  N#CCC#N   
107    gdb 110       C#CCC=O  C#CCC=O   
108    gdb 111       N#CCC=O  N#CCC=O   
109    gdb 112  [H]/N=C/NC=O  N=CNC=O   

                                                  mol  HOMO(HARTREE)  \
0    <rdkit.Chem.rdchem.Mol object at 0x7363a25f4540>        -0.3877   
1    <rdkit.Chem.rdchem.Mol object at 0x7363a25f44f0>        -0.2570   
2    <rdkit.Chem.rdchem.Mol object at 0x7363a26485e0>        -0.2928   
3    <rdkit.Chem.rdchem.Mol object at 0x7363a16868b0>        -0.2845   
4    <rdkit.Chem.rdchem.Mol object at 0x7363a1623450>        -0.3604   
..                                                ...            ...   
105  <rdkit.Chem.rdchem.Mol object at 0x7363a15b34a0>        -0.2911   
106  <rdkit.Chem.rdchem.Mol object at 0x7363a15b3770>        -0.3494   
107  <rdkit.Chem.rdchem.Mol object at 0x7363a15b3720>        -0.2583   
108  <rdkit.Chem.rdchem.Mol object at 0x7363a15b3680>        -0.2868   
109  <rdkit.Chem.rdchem.Mol object at 0x7363a15b32c0>        -0.2491   

     LUMO(HARTREE)  gap(HARTREE)   HOMO(eV)  LUMO(eV)    gap(ev)  GAP_xtb(eV)  \
0           0.1171        0.5048 -10.549854  3.186453  13.736308    17.372269   
1           0.0829        0.3399  -6.993326  2.255824   9.249150    12.228695   
2           0.0687        0.3615  -7.967494  1.869422   9.836916    14.400088   
3           0.0506        0.3351  -7.741639  1.376896   9.118535     7.287097   
4           0.0191        0.3796  -9.806984  0.519737  10.329442     5.950167   
..             ...           ...        ...       ...        ...          ...   
105         0.0111        0.3022  -7.921234  0.302046   8.223281     5.595991   
106        -0.0151        0.3344  -9.507658 -0.410892   9.099487     5.471844   
107        -0.0337        0.2245  -7.028701 -0.917024   6.108956     3.733713   
108        -0.0568        0.2300  -7.804226 -1.545607   6.258619     3.853747   
109        -0.0216        0.2276  -6.778356 -0.587766   6.193311     3.520791   

     MO_DIP_xtb (eV)  HOMO_xtb(eV)  LUMO_xtb(eV)  dif_homo(kcal/mol)  \
0              0.000      -12.7208        4.6515         1362.268389   
1              1.786      -10.5062        1.7225         2204.328305   
2              2.218      -12.1474        2.2527         2622.891124   
3              0.003      -11.5117       -4.2246         2365.713075   
4              2.622      -12.2418       -6.2916         1527.847340   
..               ...           ...           ...                 ...   
105            3.596      -11.4653       -5.8694         2223.901120   
106            4.000      -12.2363       -6.7644         1712.222682   
107            2.507      -11.1124       -7.3787         2562.521117   
108            1.578      -11.8488       -7.9951         2537.970492   
109            4.359      -10.9121       -7.3913         2593.924198   

     dif_lumo(kcal/mol)  dif_gap(kcal/mol)  
0            919.316802        2281.566036  
1            334.660748        1869.664108  
2            240.506807        2863.390369  
3           3514.938823        1149.227557  
4           4274.114264        2747.995230  
..                  ...                ...  
105         3872.582606        1648.624668  
106         3986.826315        2276.346373  
107         4054.701873        1490.465300  
108         4047.057029        1509.057283  
109         4269.217624        1677.006327  

[110 rows x 17 columns]

In [27]:
DF_dFT.to_csv('my_XTB_CREST_GDB9.csv', index=False)   # Save with index